In [ ]:
# ..... build coexp network with pseudobulk exp data ..... #

In [2]:
library(dplyr)

In [3]:
## create coexpression network ## 
build_coexp_network <- function(net, method = "spearman", flag = "rank"){
    
    # Calculate correlation coefficients
    genes = rownames(net)
    net = net[rowSums(net) > 0, ]

#     print(paste0("... ",dim(net)[1]," of ",length(genes), " genes have non-zero expression" ))

    net = cor(t(net), method = method)
    
    # Create network
    temp = net[upper.tri(net, diag = T)]
    if (flag == "abs"){
        temp = abs(temp)
    }
    
#     print("...ranking")
    temp = rank(temp, ties.method = "average")  

#     print("...reconstructing matrix")
    net[upper.tri(net, diag = T)] = temp

    net = t(net)
    net[upper.tri(net, diag = T)] = temp

    net = net / max(net, na.rm = T)
    med = median(net, na.rm = T)

    ind = setdiff(genes, rownames(net))   # which genes are missing?

    temp = matrix(med, length(ind), dim(net)[2])
    rownames(temp) = ind

    net = rbind(net, temp)
    temp = matrix(med, dim(net)[1], length(ind))
    colnames(temp) = ind
    net = cbind(net, temp)

    # reorder to original
    net = net[genes, genes]
    diag(net) = 1

    return(net)
}

In [8]:
currspecies = 'turtle'
currstage = 'stage21'
load(paste0(currstage, '_pseudobulk_expression_matrices.Rdata'))
scbulk1[1:2,]

Smooth_Muscle_Cells Immature_Endothelium Immature_FB-like
OTX2         0                   0                    0               
LOC101934893 0                   0                    0               
             Fibroblasts Pericytes_Stromal Cardiomyocytes Immature_Neuralcrest
OTX2         0           0                 0.0000000      0                   
LOC101934893 0           0                 0.1358559      0                   
             Endothelial_Capillaries Epicardium_FB-like Endocardial
OTX2         0                       0                  0          
LOC101934893 0                       0                  0          
             Endothelial_Venous Epicardium_Proliferating Pericytes
OTX2         0                  0                        0        
LOC101934893 0                  0                        0        
             Epicardium_Meso Endothelial_Arterial Immature_Cardiomyocytes
OTX2         0               0                    0                      
LOC101934893 0               0                    0                      
             Lymphoid_Immune_Cells Myeloid_Immune_Cells
OTX2         0                     0                   
LOC101934893 0                     0

In [9]:
# correlate across all subclasses
options(warn = -1)
cor1 = build_coexp_network(scbulk1, method = 'spearman')
dim(cor1)
cor1[1:3,1:3]

# save
fileo = paste0(currspecies, '_', currstage, '_coexp_net.Rdata')
save(cor1, file = fileo)

[1] 26230 26230

OTX2      LOC101934893 EXOC5    
OTX2         1.0000000 0.5000926    0.5000926
LOC101934893 0.5000926 1.0000000    0.1176039
EXOC5        0.5000926 0.1176039    1.0000000